In [205]:
import numpy as np  # linear algebra
import pandas as pd  # data processing, CSV file I/O (e.g. pd.read_csv)
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from sklearn.model_selection import train_test_split
from keras.models import Model
from keras.layers import LSTM, Dense, Dropout, Input
from sklearn.preprocessing import OneHotEncoder, LabelEncoder, MultiLabelBinarizer
from keras.layers.embeddings import Embedding
from sklearn import metrics
import re
from keras.models import Sequential
from sklearn.metrics import hamming_loss,accuracy_score,jaccard_score,zero_one_loss,classification_report
from random import seed
from random import randint
from keras.metrics import top_k_categorical_accuracy

In [133]:
import tensorflow as tf

In [7]:
def clean_text(s):
  s = s.replace("[", "")
  s = s.replace("]", "")
  s = s.replace("(", "")
  s = s.replace(")", "")
  s = s.replace(",", "")
  s = s.replace(".", "")
  s = s.replace("-", " ")
  s = s.replace("'", "")
  s = s.replace("?", "")
  s = s.lower()
  return s

In [8]:
# Read in the diagnosis file and make a pandas dataframe out of it
with open("diagnosis_new.csv") as file:
    all_lines = file.readlines()

# print (all_lines)
# print(len(all_lines))
hadm_id = []
diags = []
for lines in all_lines[1:]:
  hadm_id.append(lines[0:6])
  d = lines[9:-1]
  d = re.sub('\d+', '', d)
  d = clean_text(d)
  diags.append(d)
  
diagnosis = pd.DataFrame(list(zip(hadm_id, diags)), 
               columns =['HADM_ID', 'DIAGNOSIS'])

print(diagnosis)

      HADM_ID                                          DIAGNOSIS
0      107527   tracheomalacia status post tracheal and left ...
1      167118  copd coronary artery disease/atypical angina l...
2      196489  primary:  chronic obstructive pulmonary diseas...
3      135453   cervical spondylosis with calcification of po...
4      170490                                      brain lesion"
5      134727                                         pneumonia"
6      114236                           left sided brain lesion"
7      163469                                 avm radionecrosis"
8      189681                     skull defect s/p cranioplasty"
9      121936   severe aortic stenosis  coronary artery disea...
10     139574   rapid atrial fibrillation  congestive heart f...
11     103786  primary diagnosis: cardiac tamponade gi bleedi...
12     124073    metastatic melanoma with metastases to the l...
13     120644  chronic renal failure acute on chronic systoli...
14     128319  primary: c

In [9]:
# Combine the multiple diagnoses for one id to one diagnosis for that id 
diag_dict = {}
for i in range(0, len(diagnosis)): 
  if diag_dict.get(diagnosis.iloc[i, 0], -1) == -1:
    diag_dict[(np.int64)(diagnosis.iloc[i, 0])] = diagnosis.iloc[i, 1]
  else:
    if diag_dict[(np.int64)(diagnosis.iloc[i, 0])] == diagnosis.iloc[i, 1]:
      continue
    else:
      diag_dict[(np.int64)(diagnosis.iloc[i, 0])] += diagnosis.iloc[i, 1]

diag_dict

{107527: ' tracheomalacia status post tracheal and left main stem bronchial stent placement  hypertension  hypothyroidism  restrictive lung defect  depression"',
 167118: 'copd coronary artery disease/atypical angina lad % rca % ef % hypercholesterolemia hypothyroidism hypertension hiatal hernia cerebral vascular accidents/p motor vehicle colision > head injury & rib fracture tbm  s/p tracheoplasty"',
 196489: 'primary:  chronic obstructive pulmonary disease exacerbation  respiratory failure with intubation  upper gastrointestinal bleed/peptic ulcer disease  hypertension  anxiety"',
 135453: ' cervical spondylosis with calcification of posterior longitudinal ligament  fracture dislocation c c  ossification of the posterior longitudinal ligament  aspiration pneumonia"',
 170490: 'brain lesion"',
 134727: 'pneumonia"',
 114236: 'left sided brain lesion"',
 163469: 'avm radionecrosis"',
 189681: 'skull defect s/p cranioplasty"',
 121936: ' severe aortic stenosis  coronary artery disease w

In [10]:
# This create a pandas dataframe from the diag_dict dictionary containing all the unique diagnoses
hadm_id = []
diag = []

for k, v in diag_dict.items():
    hadm_id.append(k)
    diag.append(v)
    
unique_diags = pd.DataFrame(list(zip(hadm_id, diag)), 
               columns=['HADM_ID', 'DIAGNOSIS'])

print(unique_diags)

       HADM_ID                                          DIAGNOSIS
0       107527   tracheomalacia status post tracheal and left ...
1       167118  copd coronary artery disease/atypical angina l...
2       196489  primary:  chronic obstructive pulmonary diseas...
3       135453   cervical spondylosis with calcification of po...
4       170490                                      brain lesion"
5       134727                                         pneumonia"
6       114236                           left sided brain lesion"
7       163469                                 avm radionecrosis"
8       189681                     skull defect s/p cranioplasty"
9       121936   severe aortic stenosis  coronary artery disea...
10      139574   rapid atrial fibrillation  congestive heart f...
11      103786  primary diagnosis: cardiac tamponade gi bleedi...
12      124073    metastatic melanoma with metastases to the l...
13      120644  chronic renal failure acute on chronic systoli...
14      12

In [11]:
# Reading in the ICD csv
icd_map = pd.read_csv("icd_admsn.csv")
icd_map.drop(icd_map.columns[[0]], axis=1, inplace=True)
print(icd_map)

# for i in range(0, len(icd_map)):
#   icd_map.iloc[i, 0] = (icd_map.iloc[i, 0])
  
print(type(icd_map.iloc[0, 0]))
# icd = pd.read_csv('icd_admsn.csv')
# code_list = []

# for i in range(0, len(icd)):
# #   code = []
#   icd.iloc[i, 2] = icd.iloc[i, 2].replace("[", "")
#   icd.iloc[i, 2] = icd.iloc[i, 2].replace("]", "")
#   icd.iloc[i, 2] = icd.iloc[i, 2].replace("'", "")


#   if (icd.iloc[i, 2].find(", ") != -1):
#     code = icd.iloc[i, 2].split(", ")
#     code_list.append(code)
#   else: code_list.append(icd.iloc[i, 2])
  
print(icd_map)

       HADM_ID                                          ICD9_CODE
0       100001                                           ['5849']
1       100003                                           ['4019']
2       100007                                   ['5570', '4019']
3       100009                 ['41401', '25000', '2859', '4019']
4       100011                                          ['86121']
5       100012                                  ['41401', '4019']
6       100018                ['6827', '42731', 'V5861', '41401']
7       100020                          ['5849', '4019', '53081']
8       100021                                  ['4019', '42731']
9       100024                         ['41401', '4019', '42731']
10      100025                                           ['7756']
11      100028                                 ['99591', '42731']
12      100030                                           ['2859']
13      100031                ['42731', '4019', '73300', '53081']
14      10

In [12]:
# Merging the icd_map file and the diagnosis description file

# print(type(unique_diags.iloc[0, 0]), type(icd_map.iloc[0, 1]))

mapped_diagnosis = pd.merge(unique_diags, icd_map)

for i in range(0, len(mapped_diagnosis)):
#   code = []
  mapped_diagnosis.iloc[i, 2] = mapped_diagnosis.iloc[i, 2].replace("[", "")
  mapped_diagnosis.iloc[i, 2] = mapped_diagnosis.iloc[i, 2].replace("]", "")
  mapped_diagnosis.iloc[i, 2] = mapped_diagnosis.iloc[i, 2].replace("'", "")


#   if (icd.iloc[i, 2].find(", ") != -1):
#     code = icd.iloc[i, 2].split(", ")
#     code_list.append(code)
#   else: code_list.append(icd.iloc[i, 2])
  
# print(code_list)


print(mapped_diagnosis)

# unique_diags['ICD_CODES'] = ""

# for i in range(0, len(unique_diags)):
#   for j in range(0, len(icd_map)):
#     if unique_diags.iloc[i, 0] == icd_map.iloc[j, 1]:
#       unique_diags.iloc[i, 2] = (icd_map.iloc[j, 2])
      
# print(unique_diags)

       HADM_ID                                          DIAGNOSIS  \
0       107527   tracheomalacia status post tracheal and left ...   
1       196489  primary:  chronic obstructive pulmonary diseas...   
2       135453   cervical spondylosis with calcification of po...   
3       170490                                      brain lesion"   
4       134727                                         pneumonia"   
5       114236                           left sided brain lesion"   
6       189681                     skull defect s/p cranioplasty"   
7       121936   severe aortic stenosis  coronary artery disea...   
8       139574   rapid atrial fibrillation  congestive heart f...   
9       103786  primary diagnosis: cardiac tamponade gi bleedi...   
10      124073    metastatic melanoma with metastases to the l...   
11      120644  chronic renal failure acute on chronic systoli...   
12      128319  primary: cellulitis secondary: atrial fibrilla...   
13      188132                    

In [13]:
code_list_pre = []

for i in range(0, len(mapped_diagnosis)):
  code_list_pre.append(mapped_diagnosis.iloc[i, 2])

code_list = []
code = []
for i in range(0, len(mapped_diagnosis)):
  code = []
  if mapped_diagnosis.iloc[i, 2].find(",") != -1:
    code = mapped_diagnosis.iloc[i, 2].split(", ")
    code_list.append(code)
  else:
    code.append(mapped_diagnosis.iloc[i, 2])
    code_list.append(code)
    
print(code_list, len(code_list))

[['2449'], ['5849', '41401', '2724', '2449', '4019'], ['42731'], ['53081'], ['4019', 'V5861'], ['4019', '42731', 'V5861'], ['53081'], ['5849', '2724', '4019', '42731', '25000'], ['42731', '53081', '5849'], ['42731'], ['42731', '4019', '41401'], ['5849', '41401', '28521', '42731', '2724', 'V5861'], ['41401', '42731', 'V5861', '2724', '2859'], ['42731', '4019'], ['42731', '5849', '4019'], ['2859', '4019'], ['4019', '2724'], ['99591'], ['5849', '42731', '28521', '53081', '2449', '73300', 'V5861'], ['41401'], ['34982', '42731', '53081', '2449', '4019'], ['5849'], ['53081', '4019'], ['41401', '25000', 'V5861'], ['5849'], ['4019', '2859'], ['42731', '2859'], ['2859', '53081'], ['5849', '41401', '42731', '25000', '4019'], ['5849', '4019', '2859'], ['42731', 'V5861', '4019', '2859'], ['2859', '4019', '53081', '73300'], ['4019', '2724'], ['25000', '4019'], ['5849', '42731', '25000', '4019'], ['5849', '25000', '4019', '2859'], ['5849', '25000', '2724'], ['5849', '2859'], ['25000', '2724'], ['414

In [14]:
uni_codes = []
for i in range(0, len(code_list)):
  for j in range(0, len(code_list[i])):
    if code_list[i][j] not in uni_codes:
      uni_codes.append(code_list[i][j])
      
print(uni_codes)
print(len(uni_codes))

['2449', '5849', '41401', '2724', '4019', '42731', '53081', 'V5861', '25000', '28521', '2859', '99591', '73300', '34982', '2948', '5570', '4240', '2809', '78061', '86121', '99859', '27651', '3310', '99673', 'V173', '70901', '2752', '6827', '41091', '2858', '2532', '1984', '7080', '81000', '58181', '75733', '7756', '74686']
38


In [15]:
one_hot = MultiLabelBinarizer()
val = one_hot.fit_transform(code_list)
# one_hot.inverse_transform(val[-2:-1])
len(val)

38794

In [102]:
valnew = one_hot.fit_transform(code_list1)
# one_hot.inverse_transform(val[-2:-1])
len(valnew)

38794

In [16]:
mapped_diagnosis.head()

HADM_ID                                          DIAGNOSIS  \
0   107527   tracheomalacia status post tracheal and left ...   
1   196489  primary:  chronic obstructive pulmonary diseas...   
2   135453   cervical spondylosis with calcification of po...   
3   170490                                      brain lesion"   
4   134727                                         pneumonia"   

                       ICD9_CODE  
0                           2449  
1  5849, 41401, 2724, 2449, 4019  
2                          42731  
3                          53081  
4                    4019, V5861

In [17]:
diagnoses = list(mapped_diagnosis['DIAGNOSIS'])
print(diagnoses[0])
print(code_list[0])

 tracheomalacia status post tracheal and left main stem bronchial stent placement  hypertension  hypothyroidism  restrictive lung defect  depression"
['2449']


In [ ]:
tokenizer = Tokenizer(
    num_words = None,
    char_level=False,
    lower=True,
    split = ' ',
    filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n'
)
tokenizer.fit_on_texts(diagnoses)
sequences = tokenizer.texts_to_sequences(diagnoses)
print(sequences[0])
max_len = 0
for i in sequences:
  l = len(i)
  if max_len < l:
    max_len = l
    
print(max_len)

padded_sequences = pad_sequences(sequences, maxlen=900)

#tokenizer.word_index gives us the size of the token vocab
vocab_size = len(tokenizer.word_index) + 1
print(vocab_size)

In [130]:
print(diagnoses[0])
print(sequences[0])
tokenizer.fit_on_texts(code_list1)
arr=[]
for x in code_list1:
    sequences_new=tokenizer.texts_to_sequences(x)
    arr.append(sequences_new)
#sequences_new=tokenizer.texts_to_sequences(code_list1[:3])
print(arr[1])
padnew=[]
for x in arr:
    padnew.append(pad_sequences(x, maxlen=900))
padded_sequences_new = pad_sequences(arr[1], maxlen=900)

print(padnew[1])

#print (padded_sequences_new)
#print (padded_sequences[0])


 tracheomalacia status post tracheal and left main stem bronchial stent placement  hypertension  hypothyroidism  restrictive lung defect  depression"
[1052, 11, 9, 574, 14, 16, 818, 1250, 1665, 99, 96, 8, 77, 856, 88, 572, 61]
[[36, 111, 27, 1322], [30, 2515, 33, 1270, 30, 26], [1399, 38, 1322, 70], [1322, 227, 109], [1322, 1480, 31]]
[[   0    0    0 ...  111   27 1322]
 [   0    0    0 ... 1270   30   26]
 [   0    0    0 ...   38 1322   70]
 [   0    0    0 ... 1322  227  109]
 [   0    0    0 ... 1322 1480   31]]


In [203]:
print(len(padded_sequences))

38794


In [215]:
seed(1)
mid_value = randint(0, 38794)
start=randint(0,mid_value)
end=randint(mid_value,38794)

In [248]:
y_train[:10]

array([[0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0,
        1

In [223]:
x_test = padded_sequences[start:end].copy()
x_train = padded_sequences[0:start].copy()
x_train=np.concatenate((x_train,padded_sequences[end:]),axis=0)

y_test = val[start:end].copy()
y_train = val[0:start].copy()
y_train=np.concatenate((y_train,val[end:]),axis=0)

In [257]:
x_train = padded_sequences[0:3088].copy()
x_test = padded_sequences[3088:].copy()

y_train = val[0:3088].copy()
y_test = val[3088:].copy()
print(x_train)
print(y_train)

[[   0    0    0 ...   88  572   61]
 [   0    0    0 ...    3    8  132]
 [   0    0    0 ... 2290   92   22]
 ...
 [   0    0    0 ...  465   27  101]
 [   0    0    0 ...   27   80   22]
 [   0    0    0 ... 1320  630 7839]]
[[0 1 0 ... 0 0 0]
 [0 1 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 1 ... 0 0 0]
 [0 0 0 ... 0 0 1]
 [0 0 1 ... 0 0 0]]


In [131]:
y_train_new = padnew[0:3088].copy()
y_test_new = padnew[3088:].copy()

In [20]:

data = {'Diagnosis':'diagnoses', 'Code':'code_list'} 
df = pd.DataFrame(data) 
print(df)

ValueError: If using all scalar values, you must pass an index

In [90]:
#print(diagnoses[0])
def convert(s): 
  
    # initialization of string to "" 
    new = ";" 
  
    # traverse in the string  
    new=new.join(s)
        
        
  
    # return string  
    return new 

convert(["hello ok","ok bye"])

'hello ok;ok bye'

In [94]:
import csv
mydict={}
with open('icdcodes.csv', mode='r') as infile:
    reader = csv.reader(infile)
    for rows in reader:
        mydict[rows[0]] = rows[1]
        
#print(mydict)



#print(code_list[1])
code_list1=code_list.copy()
#code_list1 = mapped_diagnosis['ICD9_CODE']
print(mydict['1166'])
    
print(code_list1[1])
#print(code_list1[1].replace(code_list1[1],mydict[code_list1[3]]))

#for i in range (0,len(code_list1)):
#    code_list1[i]= code_list1[i].split (",")
#print(convert(code_list1[1]))
#print(code_list1[1])

for i in range (0,len(code_list1)):
    for j in range (0,len(code_list1[i])):
        #print(mydict[code_list1[i][j]])
        code_list1[i][j]=code_list1[i][j].replace(code_list1[i][j],mydict[code_list1[i][j]])

#data=pd.read_csv("icdcodes.csv")

#print(code_list1[0])
print(code_list1[0])

Tuberculous pneumonia [any form], tubercle bacilli not found by bacteriological or histological examination, but tuberculosis confirmed by other methods [inoculation of animals]
['Acute kidney failure, unspecified', 'Coronary atherosclerosis of native coronary artery', 'Other and unspecified hyperlipidemia', 'Unspecified acquired hypothyroidism', 'Unspecified essential hypertension']


KeyError: 'Unspecified acquired hypothyroidism'

In [96]:
print(code_list1[1])

['Acute kidney failure, unspecified', 'Coronary atherosclerosis of native coronary artery', 'Other and unspecified hyperlipidemia', 'Unspecified acquired hypothyroidism', 'Unspecified essential hypertension']


In [97]:
data = {'diagnoses':diagnoses,'icd_def':code_list1}
temp_df = pd.DataFrame(data)

In [99]:
temp_df.to_csv('text_to_text.csv')

In [93]:
#code_list1[52]=clean_text(convert(code_list1[52]))
#code_list1[1]=clean_text(code_list1[1])
#print(code_list1[52])

for i in range (0,len(code_list1)):
    code_list1[i]=clean_text(convert(code_list1[i]))
    print(code_list1[i])

#print(diagnoses[0])
d1=pd.DataFrame(diagnoses,columns=['DD'])
#print(d1)
d2=pd.DataFrame(code_list1,columns=['ICDD'])
#print(d2)
df = pd.concat([d1.reset_index(drop=True),d2.reset_index(drop=True)], axis=1)

#df = pd.DataFrame(data, columns = ['DD', 'ICDD']) 

unspecified acquired hypothyroidism
acute kidney failure unspecified;coronary atherosclerosis of native coronary artery;other and unspecified hyperlipidemia;unspecified acquired hypothyroidism;unspecified essential hypertension
atrial fibrillation
esophageal reflux
unspecified essential hypertension;long term current use of anticoagulants
unspecified essential hypertension;atrial fibrillation;long term current use of anticoagulants
esophageal reflux
acute kidney failure unspecified;other and unspecified hyperlipidemia;unspecified essential hypertension;atrial fibrillation;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled
atrial fibrillation;esophageal reflux;acute kidney failure unspecified
atrial fibrillation
atrial fibrillation;unspecified essential hypertension;coronary atherosclerosis of native coronary artery
acute kidney failure unspecified;coronary atherosclerosis of native coronary artery;anemia in chronic kidney disease;at

iron deficiency anemia unspecified
acute kidney failure unspecified;anemia unspecified
acute kidney failure unspecified;dehydration;atrial fibrillation;mitral valve disorders;coronary atherosclerosis of native coronary artery;unspecified acquired hypothyroidism;anemia unspecified
acute kidney failure unspecified
acute kidney failure unspecified;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;coronary atherosclerosis of native coronary artery
acute kidney failure unspecified;anemia unspecified;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled
coronary atherosclerosis of native coronary artery;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;other and unspecified hyperlipidemia;unspecified essential hypertension;esophageal reflux
anemia in chronic kidney disease
anemia in chronic kidney disease
mitral valve disorders
atria

dehydration
cellulitis and abscess of foot except toes;coronary atherosclerosis of native coronary artery
coronary atherosclerosis of native coronary artery
acute kidney failure unspecified;atrial fibrillation;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled
acute kidney failure unspecified;anemia unspecified
atrial fibrillation;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;unspecified acquired hypothyroidism;unspecified essential hypertension;anemia unspecified
anemia unspecified
atrial fibrillation;other persistent mental disorders due to conditions classified elsewhere;anemia unspecified
mitral valve disorders;acute kidney failure unspecified;atrial fibrillation;iron deficiency anemia unspecified
iron deficiency anemia unspecified
mitral valve disorders;atrial fibrillation;long term current use of anticoagulants;anemia unspecified
coronary atherosclerosis of native coro

other and unspecified hyperlipidemia
unspecified essential hypertension
atrial fibrillation;other and unspecified hyperlipidemia
coronary atherosclerosis of native coronary artery;other and unspecified hyperlipidemia;atrial fibrillation
acute kidney failure unspecified;atrial fibrillation;coronary atherosclerosis of native coronary artery;unspecified essential hypertension;other and unspecified hyperlipidemia;osteoporosis unspecified
atrial fibrillation;unspecified essential hypertension;anemia unspecified;coronary atherosclerosis of native coronary artery;long term current use of anticoagulants
disorders of magnesium metabolism
diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;iron deficiency anemia unspecified
acute kidney failure unspecified;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;atrial fibrillation;anemia unspecified
atrial fibrillation;anemia unspecified
acute k

acute kidney failure unspecified;atrial fibrillation;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled
other postoperative infection;sepsis;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;other and unspecified hyperlipidemia;unspecified essential hypertension
diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;atrial fibrillation;unspecified essential hypertension
acute kidney failure unspecified;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;unspecified essential hypertension
acute kidney failure unspecified;anemia in chronic kidney disease
other and unspecified hyperlipidemia;coronary atherosclerosis of native coronary artery
coronary atherosclerosis of native coronary artery;other and unspecified hyperlipidemia
toxic encephalopathy;acute kidney failure unspecified

...

dehydration;atrial fibrillation;unspecified essential hypertension;alzheimers disease
long term current use of anticoagulants
unspecified acquired hypothyroidism;unspecified essential hypertension
acute vascular insufficiency of intestine;unspecified acquired hypothyroidism;unspecified essential hypertension;atrial fibrillation
unspecified acquired hypothyroidism;unspecified essential hypertension
unspecified essential hypertension;unspecified acquired hypothyroidism
acute kidney failure unspecified;esophageal reflux;unspecified acquired hypothyroidism
unspecified essential hypertension
acute kidney failure unspecified;unspecified essential hypertension
anemia in chronic kidney disease
mitral valve disorders;coronary atherosclerosis of native coronary artery;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;unspecified essential hypertension;anemia unspecified
coronary atherosclerosis of native coronary artery;atrial fibrillation
d

atrial fibrillation;osteoporosis unspecified
atrial fibrillation;long term current use of anticoagulants;esophageal reflux;unspecified acquired hypothyroidism
atrial fibrillation;anemia unspecified;unspecified acquired hypothyroidism;esophageal reflux;coronary atherosclerosis of native coronary artery
unspecified essential hypertension
atrial fibrillation;unspecified essential hypertension;other and unspecified hyperlipidemia;unspecified acquired hypothyroidism;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled
unspecified essential hypertension;other and unspecified hyperlipidemia
contusion of lung without mention of open wound into thorax;unspecified essential hypertension
anemia unspecified
coronary atherosclerosis of native coronary artery
acute kidney failure unspecified;coronary atherosclerosis of native coronary artery;mitral valve disorders;other and unspecified hyperlipidemia;unspecified acquired hypothyroidism;anemia in ch

atrial fibrillation;other and unspecified hyperlipidemia
unspecified essential hypertension;other and unspecified hyperlipidemia;coronary atherosclerosis of native coronary artery;esophageal reflux;osteoporosis unspecified;unspecified acquired hypothyroidism
alzheimers disease;iron deficiency anemia unspecified
unspecified essential hypertension;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;alzheimers disease;coronary atherosclerosis of native coronary artery
unspecified acquired hypothyroidism;esophageal reflux
unspecified acquired hypothyroidism;esophageal reflux;long term current use of anticoagulants
acute kidney failure unspecified;dehydration
atrial fibrillation;unspecified essential hypertension
acute kidney failure unspecified;anemia unspecified
dehydration;unspecified essential hypertension;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled
atrial fibrillation;unspe

acute kidney failure unspecified;other and unspecified hyperlipidemia;long term current use of anticoagulants
acute kidney failure unspecified;long term current use of anticoagulants;atrial fibrillation;other persistent mental disorders due to conditions classified elsewhere
unspecified essential hypertension
coronary atherosclerosis of native coronary artery;atrial fibrillation;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;unspecified essential hypertension
acute kidney failure unspecified
acute kidney failure unspecified
acute kidney failure unspecified
coronary atherosclerosis of native coronary artery;other and unspecified hyperlipidemia;unspecified acquired hypothyroidism;atrial fibrillation
unspecified essential hypertension;anemia unspecified
acute kidney failure unspecified;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;other and unspecified hyperlipidemia;atrial

sepsis
coronary atherosclerosis of native coronary artery
acute kidney failure unspecified
unspecified essential hypertension
unspecified acquired hypothyroidism;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;unspecified essential hypertension
unspecified essential hypertension
acute kidney failure unspecified;atrial fibrillation;mitral valve disorders
unspecified essential hypertension
osteoporosis unspecified
other postoperative infection;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;unspecified essential hypertension;esophageal reflux;anemia unspecified
anemia unspecified
long term current use of anticoagulants;coronary atherosclerosis of native coronary artery
coronary atherosclerosis of native coronary artery;diabetes mellitus without mention of complication type ii or unspecified type not stated as uncontrolled;unspecified essential hypertension
unspecified essenti

In [86]:
print(df)


                                                      DD  \
0       tracheomalacia status post tracheal and left ...   
1      primary:  chronic obstructive pulmonary diseas...   
2       cervical spondylosis with calcification of po...   
3                                          brain lesion"   
4                                             pneumonia"   
5                               left sided brain lesion"   
6                         skull defect s/p cranioplasty"   
7       severe aortic stenosis  coronary artery disea...   
8       rapid atrial fibrillation  congestive heart f...   
9      primary diagnosis: cardiac tamponade gi bleedi...   
10       metastatic melanoma with metastases to the l...   
11     chronic renal failure acute on chronic systoli...   
12     primary: cellulitis secondary: atrial fibrilla...   
13                                       lower gi bleed"   
14                          primary diagnosis: colon ca"   
15                      primary: pcp pne

In [87]:
 df.to_csv('main.csv') 


In [161]:
def ham(y_true,y_pred):
    return hamming_loss(y_true,y_pred)

In [289]:
inputs = Input(shape=(900, ))
embedding_layer = Embedding(vocab_size,
                            128,
                            input_length=900)(inputs)

x = LSTM(64)(embedding_layer)
x = Dense(32, activation='relu')(x)
predictions = Dense(38, activation='softmax')(x)
model = Model(inputs=[inputs], outputs=predictions)

model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['categorical_accuracy','top_k_categorical_accuracy','precision'])

model.summary()

model.fit(x_train, y_train, epochs=2, batch_size=500)

ValueError: Unknown metric function:precision

In [287]:
model.evaluate(x_test,y_test, verbose=0)


[0.2609781549336536, 0.1890438581776006, 0.45205287626896334]

In [236]:
loss, accuracy = model.evaluate(x_test, y_test, verbose=0)
#print(metrics.confusion_matrix(y_test, y_pred))
print('Accuracy: %f' % (accuracy*100))

ValueError: Error when checking model target: the list of Numpy arrays that you are passing to your model is not the size the model expected. Expected to see 1 array(s), but instead got the following list of 35706 arrays: [array([[   0,    0,    0, ...,  111,   27, 1322],
       [   0,    0,    0, ...,    0,   47,   52],
       [   0,    0,    0, ...,    0,    0,   13],
       [   0,    0,    0, ..., 1322, 1480,   31],...

In [259]:
oinx=0
iinx=0
for x in y_pred:
    #print(x)
    iinx=0
    for y in x:
        if y>=0.5:
            #print(y)
            y_pred[oinx][iinx]=1
        else:
            #print(y)
            y_pred[oinx][iinx]=0
        iinx=iinx+1
    oinx=oinx+1    
y_pred = y_pred.astype(int)
#print(y_pred[:10])
#y_pred1=one_hot.inverse_transform(y_pred)
#print(y_pred1)
#print(val)

In [194]:
print(len(y_test[0]))

38


In [196]:
print(len(y_pred[0]))

38


In [ ]:
print(one_hot.inverse_transform(val[-2:-1]))

In [170]:
np.pad(y_true,(0,1),'constant')

array(['4273', '4019', '7330', 'V53081', '0'], dtype='<U6')

In [157]:
y_pred1=np.argmax(y_pred, axis=1)
y_test1=np.argmax(y_test, axis=1)
#print(y_pred[1])
#print(y_test1[1])

In [156]:
y_pred1 = (y_pred > 0.5) 
print(y_pred1[0])

[False False False False False False False False False False False False
 False False False False False False False False False False False False
 False False False False False False False False False False False False
 False False]


In [262]:
y_pred=model.predict(x_test,verbose=1)

35706/35706 [==============================] - 185s 5ms/step


In [263]:
oinx=0
iinx=0
for x in y_pred:
    #print(x)
    iinx=0
    for y in x:
        if y>=0.5:
            #print(y)
            y_pred[oinx][iinx]=1
        else:
            #print(y)
            y_pred[oinx][iinx]=0
        iinx=iinx+1
    oinx=oinx+1    
y_pred = y_pred.astype(int)

In [264]:
print(hamming_loss(y_test, y_pred))

0.0693595651033145


In [280]:
from keras.metrics import top_k_categorical_accuracy
#print(accuracy(y_test,y_pred))
print(top_k_categorical_accuracy(y_test, y_pred, k=5))

Tensor("Cast_6:0", shape=(35706,), dtype=float32)


In [272]:
y_find = ['V53081', 'E4019', '73300', '53081']
y_true = ['V53081', '4019', '7330']
y_true=np.pad(y_true,(0,1),'constant')
print(hamming_loss(y_find, y_true))

0.75


While using hamming_loss, length of the two sequences must be same and the order also has to be similar.

In [227]:
print(accuracy_score(y_pred,y_test))

0.0


In [228]:
print(jaccard_score(y_pred, y_test, average='samples'))

0.0


In [240]:
print(classification_report(y_test, y_pred, target_names=uni_codes))

              precision    recall  f1-score   support

        2449       0.00      0.00      0.00        30
        5849       0.00      0.00      0.00      1811
       41401       0.00      0.00      0.00      3493
        2724       0.00      0.00      0.00        25
        4019       0.00      0.00      0.00      2925
       42731       0.00      0.00      0.00        96
       53081       0.00      0.00      0.00       517
       V5861       0.00      0.00      0.00       479
       25000       0.00      0.00      0.00       583
       28521       0.00      0.00      0.00        28
        2859       0.00      0.00      0.00      1909
       99591       0.00      0.00      0.00       376
       73300       0.00      0.00      0.00       198
       34982       0.00      0.00      0.00       214
        2948       0.00      0.00      0.00      7599
        5570       0.00      0.00      0.00       135
        4240       0.00      0.00      0.00      5181
        2809       0.00    

D:\Anaconda\lib\site-packages\sklearn\metrics\classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
D:\Anaconda\lib\site-packages\sklearn\metrics\classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
D:\Anaconda\lib\site-packages\sklearn\metrics\classification.py:1437: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels.
  'precision', 'predicted', average, warn_for)


In [190]:
maxlen=0
for x in code_list:
    if maxlen<len(x):
        maxlen=len(x)
        
print(maxlen)
    

13


In [249]:
y_tr = [[0,0,0,1]]
y_pre = [[0,0,0,0]]

In [255]:
from keras import metrics

In [256]:
result = keras.metrics.accuracy(y_tr,y_pre)

AttributeError: module 'keras.metrics' has no attribute 'accuracy'